Join the data from Part 1 with the data from Part 2 to create a new dataframe.

> House Keeping

In [26]:
import pandas as pd
import os

In [ ]:
Yelp_df = pd.read_csv('Yelp_df.csv', index_col = 0)
CityBike_df = pd.read_csv('City_Bike.csv', index_col=0)
FourSquare_df = pd.read_csv('FourSquare_df.csv', index_col = 0)

In [ ]:
# Restructure columns to a consistent nomenclature 
Yelp_df.rename(columns={'category_name' : 'category', 'distance_4rm_bike' : 'Distance_from_Bike_Station'}, inplace= True)
Yelp_df.reindex(['lat', 'category', 'name', 'rating', 'reviews', 'price_scale', 'Distance_from_Bike_Station'], axis=1, inplace = True)
FourSquare_df.rename(columns={'price' : 'price_scale'}, inplace= True)

In [ ]:
# Drop redundant columns
FourSquare_df.drop(['address', 'fsq_id', 'cat_id', 'categories', 'city', 'country'], axis=1, inplace=True)
Yelp_df.drop(['business_id'], axis=1, inplace=True)


In [ ]:
# Create new POI dataframe
poi_df= pd.concat([Yelp_df, FourSquare_df], ignore_index=True)

In [ ]:
# Merge Poi dataframe to CityBike dataframe
merged_df = poi_df.merge(CityBike_df, on='lat', how='left')

> house keeping 

In [ ]:
# rename columns
merged_df.rename(columns={'name_y' : 'station_name'}, inplace= True)

In [ ]:
# export df to csv
merged_df.to_csv('merged_df.csv')

Provide a visualization that you used as part of your EDA process. Explain the initial pattern or relationship you discoved through this visualization. 

In [9]:
merged_df = pd.read_csv('/Users/patrick/Desktop/Lighthouse_labs/Statistical_Modeling/Temp notebooks/merged_df.csv', index_col=0)

In [10]:
merged_df.describe()

lat      reviews       rating  price_scale  \
count  3767.000000  3767.000000  3767.000000  3767.000000   
mean   -122.653876   419.714096     4.019512     1.785506   
std       0.039933   696.639176     0.636623     0.585424   
min    -122.759140     0.000000     0.000000     1.000000   
25%    -122.681600    88.000000     4.000000     1.000000   
50%    -122.661920   205.000000     4.000000     2.000000   
75%    -122.635050   471.500000     4.500000     2.000000   
max    -122.537570  8257.000000     5.000000     4.000000   

       Distance_from_Bike_Station     latitude  empty_slots   free_bikes  \
count                 3767.000000  3767.000000  3767.000000  3767.000000   
mean                   296.406424    45.529066     7.578179     2.533847   
std                    264.071207     0.021785     5.131172     2.820315   
min                      3.000000    45.479713     0.000000     0.000000   
25%                    139.000000    45.514182     3.000000     1.000000   
50%                    279.000000    45.525001     7.000000     2.000000   
75%                    433.000000    45.539665    11.000000     3.000000   
max                   9880.000000    45.593563    21.000000    15.000000   

       extra.renting  extra.returning       ebikes  total_bikes  
count         3767.0           3767.0  3767.000000  3767.000000  
mean             1.0              1.0     2.533847    10.393151  
std              0.0              0.0     2.820315     5.452463  
min              1.0              1.0     0.000000     2.000000  
25%              1.0              1.0     1.000000     6.000000  
50%              1.0              1.0     2.000000     9.000000  
75%              1.0              1.0     3.000000    15.000000  
max              1.0              1.0    15.000000    27.000000

In [ ]:
#pip install ydata_profiling

In [11]:
from ydata_profiling import ProfileReport

In [12]:
ProfileReport = ProfileReport(merged_df, title='ProfileReport')

In [13]:
ProfileReport.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

> There was a total of 3,767 Points of interest. The characteristics being sought are yelp reviews, rating, price scale, number of bikes, and ebikes
> There is very weak correlation between bike station related varribales and point of interest varriables. Business reviews and total bikes at station have a 0.25 correlation which is weak. Same for reviews and number of e-bikes at the station. 

# Database

Put all your results in an SQLite3 database (remember, SQLite stores its databases as files in your local machine - make sure to create your database in your project's data/ directory!)

In [14]:
# Imports 
import sqlite3
from sqlite3 import Error

Look at the data before and after the join to validate your data.

In [15]:
# create connection
def create_connection(path):
    connection = None
    try:
        connection = sqlite3.connect(path)
        print("Connection to SQLite DB successful")
    except Error as e:
        print(f"The error '{e}' occurred")

    return connection

In [16]:
connection = create_connection("sm_app.sqlite")

Connection to SQLite DB successful


In [17]:
# define function querry
def execute_query(connection, query):
    cursor = connection.cursor()
    try:
        cursor.execute(query)
        connection.commit()
        print("Query executed successfully")
    except Error as e:
        print(f"The error '{e}' occurred")

In [18]:
# Create Table

create_merged_df_table = """
CREATE TABLE IF NOT EXISTS city_bike_poi (
  id INTEGER PRIMARY KEY AUTOINCREMENT,
  lat TEXT NOT NULL,
  category TEXT,
  business_name TEXT,
  transactions TEXT,
  reviews INTEGER, 
  rating FLOAT, 
  price_scale INTEGER, 
  Distance_from_Bike_Station INTEGER
);
"""

In [19]:
execute_query(connection, create_merged_df_table)  

Query executed successfully


In [38]:
# copy csv to sql lite
# the df csv is copied to a temp folder for easy loading on a mac

copy_merged_df_table = """
COPY city_bike_poi(
    lat,
    category,
    business_name,
    transactions,
    reviews,
    rating,
    price_scale,
    Distance_from_Bike_Station)
FROM 'Temp notebooks/merged_df.csv'
DELIMITER ','
CSV HEADER
;
"""

In [ ]:
execute_query(connection, copy_merged_df_table)  